# 循环神经网络的应用背景

- 在机器人只能中，怎么训练机器人像人一样说话？考虑一个简单的情况：
    - 比如给机器人一个字：我，训练机器人说下一个字；并依次类推，让机器人说出一举完整的句子：我要学人工智能。

- 说话的训练特征是，按照输入序列，提供数据训练与输出；在1986年-1990年，M. I. Jordan，Jeffrey Elman提出循环神经网络用来处理这种类型的数据训练。

- 循环神经网络因为其复杂性，为了解决一些局部问题，在此基础上又提出很多不同的循环神经网络，比如：
    - 双向循环神经网络
    - 长短时记忆网络等。

# 循环神经网络的思路

- 循环神经网络的思路与全链接与卷积神经网络思路一样，使用的前馈误差传递的方式训练权重矩阵，但是因为其训练的数据集结构不同（序列数据集），其预测输出模型与全链接神经网络、卷积神经网络的预测输出模型不一样。

1. 如果不考虑具体的神经元的细节，从神经网络的层来看，全链接神经网络与卷积神经网络，可以使用如下示意图表示：
    - 

2. 循环神经网络的特点是循环，因为输入数据的序列性，所以需要数据按照序列输入，下面就是示意图（不考虑BP的误差传递与梯度更新的情况）：
    - 

3. 循环神经网络，就是把数据按照序列训练，上一个序列的的结果，参与下一个序列的训练。可以把上面的思路抽象成如下示意图：
    - 

- 说明：
    - 上面图示来自网络：`https://zybuluo.com/hanbingtao/note/541458`

# 循环神经网络还有很多变形

## 上下序列的关系变化

1. 使用隐藏层的输出，作为下一序列的输入合成。
    - 

2. 使用上一序列的输出层的输出，作为下一序列的输入喝成：
    - 

## 输出变化

1. 只有最后输出，不需要每个序列都输出：
    - 

## 双向循环

1. 正向 + 反向训练：每个序列的输出是由正向训练 + 反向训练的结果构成。
    - 



- 正向 + 反向  = 输出，然后再根据输出进行权重更新。

## 其他变化

- 上面的变化相对比较简单，还有一些会根据循环神经网络的梯度消失与爆炸的问题提出的循环神经网络，比如：
    - 神经历史压缩器（Neural History Compressor, NHC） 
    - 长短期记忆网络（Long Short-Term Memory networks, LSTM） 
    - 门控循环单元网络（Gated Recurrent Unit networks, GRU） 
    - 回声状态网络（echo state network）
    - 独立循环神经网络（Independent RNN）

# 循环神经网络模型

- 下面使用最简单的一种循环神经网络结构来说明循环神经的的模型、训练实现与预测。

## 输出模型

- $o_t = g(s_{t} V)$
- $s_{t+1} =f( x_{t+1} U + s_{t} W)$

- 说明：
    - 每个序列中的输出，与序列前面的输入都有关系。
    - 如果不考虑序列，输出$o_t$与前面的全链接神经网络与卷积神经网络完全一样。所以我们下面重点考虑序列循环部分的推导与原理。
    - 了解循环部分的推导与推理，才能知道这种简单的循环神经网络的一些不足，后面的一些循环神经网络就容易理解。

## 损失函数模型

- 输出层的误差项计算与损失函数有关。

- 损失函数可以使用常见的损失函数；
    - 均方差损失函数
    - log损失函数
        - 输出使用sigmoid：sigmoid交叉熵
        - 输出使用softmax：softmax交叉熵
    - hinge交叉熵损失函数
    - huber损失函数

- 在循环神经网络中，最后的损失是每个序列的的损失的和。
    - $L = \sum\limits _{t=1} ^{T} L_{t}$，其中$T$表示序列的长度 

## 梯度更新

- 上面输出模型中，有三个权重系数需要训练（如果隐藏层更多的话，这个权重系数更多），所有需要计算三个权重系数的更新梯度，我们先考虑某个序列$t$的梯度更新：
    - $V$的梯度更新：$\dfrac{\partial{L_t}}{\partial{V}}$
    
    - $U$的梯度更新：$\dfrac{\partial{L_t}}{\partial{U}}$
    
    - $W$的梯度更新：$\dfrac{\partial{L_t}}{\partial{W}}$

### $V$的梯度计算
- $\dfrac{\partial{L_t}}{\partial{V}}$计算与前面全链接神经网络的输出层计算一样：
    - $\dfrac{\partial{L_t}}{\partial{V}} = \dfrac{\partial{L_t}}{\partial{g}}  \dfrac{\partial{g}}{\partial{s_t V}} \dfrac{\partial{s_t V}}{\partial{V}}   = L_t^{\prime} g^{\prime} s_t$
    

### $W$的梯度计算

-  $\dfrac{\partial{L_t}}{\partial{W}}$的计算需要考虑在当前需要影响到误差的序列项，在$t$之前序列都影响到当前序列，所有梯度更新值使用链式求导展开：
    - $\dfrac{\partial{L_t}}{\partial{W}} = \sum\limits_{k=1}^{t}  \dfrac{\partial{L_t}}{\partial{s_k}}   \dfrac{\partial{s_k}}{\partial{W}} = \sum\limits_{k=1}^{t}  \dfrac{\partial{L_t}}{\partial{s_k}}   \dfrac{\partial{f(x_{k} U+s_{k-1}W)}}{\partial{W}} = \sum\limits_{k=1}^{t}  \dfrac{\partial{L_t}}{\partial{s_k}}   \dfrac{\partial{f(x_{k} U+s_{k-1}W)}}{\partial{(x_{k} U+s_{k-1}W)}}    \dfrac{\partial{(x_{k} U+s_{k-1}W)}}{W}$
    
    - $= \sum\limits_{k=1}^{t}  \dfrac{\partial{L_t}}{\partial{s_k}}   \dfrac{\partial{f(x_{k} U+s_{k-1}W)}}{\partial{(x_{k} U+s_{k-1}W)}}   s_{k-1}$
    
    - 可以记：$\delta _k = \dfrac{\partial{L_t}}{\partial{s_k}}   \dfrac{\partial{f(x_{k} U+s_{k-1}W)}}{\partial{(x_{k} U+s_{k-1}W)}}$
    
    - 则$\dfrac{\partial{L_t}}{\partial{W}} = \sum\limits_{k=1}^{t} \delta_k  s_{k-1}$

- 注意上面是形式上的推导，因为真正的矩阵偏导，还需要细化到矩阵的每个元素求导，这个可以了解Jacobian矩阵导数的相关知识。
    - 细节在编码的时候是需要了解清楚的。

### $U$的梯度计算

- 与上面的推导类似，$U$的梯度计算如下：
    -  $\dfrac{\partial{L_t}}{\partial{U}} = \sum\limits_{k=1}^{t} \delta_k  x_{k}$

## 误差项模型

- 根据梯度公式，$W，U$使用共同的误差项$\delta$，所以梯度的计算的关键是误差项的传递。

- 输出层的误差项的计算：$L^{\prime} f^{\prime}$
    - 损失函数的导数$L(y, y^{\prime})$
    - 输出层激活函数$f(x)$


因为每个序列都影响他之后每个序列的输出，所以每个序列的误差项都有他之后的误差项有关。这个误差项传递的算法称为：
    - Back-Propagation Through Time (BPTT)

- 误差项的传递有两个方向：
    - 按照序列传递
    - 按照层数传递

### 误差项按照序列传递

- $\delta_k = \delta_t \prod_{i=k}^{t-1}W f^{\prime}$
    - 其中$t$表示序列长度。

### 误差按照层传递

- $\delta_k^{l-1} = \delta_k^{l} U{{(f^{l-1})}^{\prime}}$

# 循环神经网络实现(tensorflow)

## 数据读取

In [118]:
import os
import re

# 读取数据
data_sms = []
with open(os.path.join('./rnn', 'SMSSpamCollection'), 'r') as fd:
    for sms in fd:
        data_sms.append(sms)

# 最后一行是空行，丢弃最后空行
data_sms = data_sms[:-1]



## 数据格式化

In [119]:
# 注意每行的短信类别使用\t分隔，每行使用\n分隔。
data_sms = [sms.split('\t') for sms in data_sms if len(sms)>=1]
# 把短信的类别与内容分成两个列表
[target, data] = [list(sms) for sms in zip(*data_sms)]


## 数据清洗

In [120]:
# 对短信内容进行清洗
new_data = []
for sms in  data:
    sms = re.sub(r'([^\s\w]|_|[0-9])+', '', sms)  # 删除不必要的符号
    sms = " ".join(sms.split())   # 去掉\n
    sms = sms.lower()   # 小写转换
    new_data.append(sms)
data =new_data

## 词向量化

In [121]:
import warnings
warnings.filterwarnings("ignore")

import tensorflow as tf
from tensorflow.contrib.learn import preprocessing
import numpy as np
# 词向量（可以使用sklearn的库）
max_sequence_length = 25
min_word_frequency = 10

# 词表处理类
vocab_processor = preprocessing.VocabularyProcessor(max_sequence_length,  min_frequency=min_word_frequency)
# vocab_processor = preprocessing.VocabularyProcessor(100)
# 转换为ndarray对象
data = np.array(list(vocab_processor.fit_transform(data)))

# 标签的数值化
target = np.array([1 if t=='ham' else 0 for t in target])


## 切分训练集与测试集

In [122]:
# 对数据集洗牌
shuffled_idx = np.random.permutation(np.arange(len(data)))

x_data = data[shuffled_idx]
y_data = target[shuffled_idx]
print(x_data.shape)
# 切分训练集与测试集
num_train = int(len(x_data)*0.80)  # 取80%作为训练集

x_train, x_test = x_data[:num_train], x_data[num_train:]
y_train, y_test = y_data[:num_train], y_data[num_train:]

vocab_size = len(vocab_processor.vocabulary_)  # 词表数量
print(F"词表数量 {vocab_size: d}")

x_train

(5573, 25)
词表数量  934


array([[359, 427,  52, ...,   8, 273, 507],
       [ 94,  40, 900, ...,   0,  78,  86],
       [  7,  83,   0, ...,  20, 681,   0],
       ...,
       [ 38,  84,   0, ...,   7, 156,   6],
       [ 82,  12,   5, ...,   0,   0,   0],
       [142,  11,   0, ...,   0,   0,   0]])

## 循环神经网络模型构建

### 对数据格式与浮点数化处理

In [123]:
import tensorflow as tf
from tensorflow.python.framework import ops
ops.reset_default_graph()
# 定义占位
x_data = tf.placeholder(tf.int32, [None, max_sequence_length])   # 该数据不符合循环神经网络格式
y_output = tf.placeholder(tf.int32, [None])
# 把输入数据转换为循环神经网络需要的数据格式（同时把数据映射成随机数：这里可以使用其他类似的词向量化技术）
embedding_mat = tf.Variable(tf.random_uniform([vocab_size, embedding_size], -1.0, 1.0))
embedding_output = tf.nn.embedding_lookup(embedding_mat, x_data)


### 循环层

In [124]:
import warnings
warnings.filterwarnings("ignore")

rnn_size = 10   # 序列数量
cell = tf.nn.rnn_cell.BasicRNNCell(num_units = rnn_size)
output, state = tf.nn.dynamic_rnn(cell, embedding_output, dtype=tf.float32)

## 输出层

In [125]:
output = tf.transpose(output, [1, 0, 2])    # 交换维度位置

last = tf.gather(output, int(output.get_shape()[0]) - 1)   # 取最后作为识别结果，gather根据下标取值

# 输出层就是全连接层
weight = tf.Variable(tf.truncated_normal([rnn_size, 2], stddev=0.1))
bias = tf.Variable(tf.constant(0.1, shape=[2]))

logits_out = tf.nn.softmax(tf.matmul(last, weight) + bias)

## 损失函数与优化器

In [126]:
import warnings
warnings.filterwarnings("ignore")

# 使用稀疏softmax交叉熵损失函数
losses = tf.nn.sparse_softmax_cross_entropy_with_logits(labels=y_output, logits=logits_out) #
loss = tf.reduce_mean(losses)

# 用来观察准确度（分类正确率）
accuracy = tf.reduce_mean(tf.cast(tf.equal(tf.argmax(logits_out, 1), tf.cast(y_output, tf.int64)), tf.float32))

optimizer = tf.train.RMSPropOptimizer(0.0005)
train_step = optimizer.minimize(loss)

## 模型训练

In [129]:
import tensorflow as tf

epochs = 20
init = tf.initialize_all_variables()
sess = tf.Session()
sess.run(init)

train_loss = []
test_loss = []
train_accuracy = []
test_accuracy = []

# 循环训练epochs轮
for epoch in range(epochs):

    # 打乱数据
    shuffled_idx = np.random.permutation(np.arange(len(x_train)))
    x_train = x_train[shuffled_idx]
    y_train = y_train[shuffled_idx]
    # 计算训练次数
    num_batches = int(len(x_train)/batch_size) + 1
    # 每批次进行一次训练
    for i in range(num_batches):
        # Select train data
        min_idx = i * batch_size
        max_idx = np.min([len(x_train), ((i+1) * batch_size)])
        x_train_batch = x_train[min_idx:max_idx]
        y_train_batch = y_train[min_idx:max_idx]
        
        # Run train step
        train_dict = {x_data: x_train_batch, y_output: y_train_batch}
        sess.run(train_step, feed_dict=train_dict)
        
    # Run loss and accuracy for training
    temp_train_loss, temp_train_acc = sess.run([loss, accuracy], feed_dict=train_dict)
    train_loss.append(temp_train_loss)
    train_accuracy.append(temp_train_acc)
    
    # Run Eval Step
    test_dict = {x_data: x_test, y_output: y_test}
    temp_test_loss, temp_test_acc = sess.run([loss, accuracy], feed_dict=test_dict)
    test_loss.append(temp_test_loss)
    test_accuracy.append(temp_test_acc)
    print(F'轮数: {epoch+1}, 测试集损失: {temp_test_loss:.2}, 测试集准确度: {temp_test_acc:.2}')

轮数: 1, 测试集损失: 0.74, 测试集准确度: 0.18
轮数: 2, 测试集损失: 0.73, 测试集准确度: 0.18
轮数: 3, 测试集损失: 0.71, 测试集准确度: 0.18
轮数: 4, 测试集损失: 0.67, 测试集准确度: 0.82
轮数: 5, 测试集损失: 0.64, 测试集准确度: 0.82
轮数: 6, 测试集损失: 0.6, 测试集准确度: 0.83
轮数: 7, 测试集损失: 0.57, 测试集准确度: 0.83
轮数: 8, 测试集损失: 0.55, 测试集准确度: 0.83
轮数: 9, 测试集损失: 0.53, 测试集准确度: 0.83
轮数: 10, 测试集损失: 0.52, 测试集准确度: 0.84
轮数: 11, 测试集损失: 0.51, 测试集准确度: 0.84
轮数: 12, 测试集损失: 0.5, 测试集准确度: 0.85
轮数: 13, 测试集损失: 0.49, 测试集准确度: 0.85
轮数: 14, 测试集损失: 0.49, 测试集准确度: 0.85
轮数: 15, 测试集损失: 0.48, 测试集准确度: 0.85
轮数: 16, 测试集损失: 0.48, 测试集准确度: 0.86
轮数: 17, 测试集损失: 0.47, 测试集准确度: 0.86
轮数: 18, 测试集损失: 0.47, 测试集准确度: 0.86
轮数: 19, 测试集损失: 0.46, 测试集准确度: 0.86
轮数: 20, 测试集损失: 0.46, 测试集准确度: 0.86


## 训练评估可视化

In [132]:
% matplotlib inline
import matplotlib.pyplot as plt

epoch_seq = np.arange(1, epochs+1)   # 定制显示x坐标，训练的轮数

plt.plot(epoch_seq, train_loss, 'b--', label='训练集t')
plt.plot(epoch_seq, test_loss, 'r-', label='测试集')
plt.title('损失值曲线')
plt.xlabel('轮数')
plt.ylabel('Softmax损失')
plt.legend(loc='upper left')
plt.show()

# Plot accuracy over time
plt.plot(epoch_seq, train_accuracy, 'b--', label='训练集')
plt.plot(epoch_seq, test_accuracy, 'r-', label='测试集')
plt.title('准确度曲线')
plt.xlabel('轮数')
plt.ylabel('准确度')
plt.legend(loc='upper left')
plt.show()

----